In [1]:
# Load packages
from datetime import datetime
import logging
import math
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import seaborn as sns
import scipy
import sys

In [2]:
# declare universal variables
CONDITION = 'control'
CONDITION_CLINICAL_DF = 'Control'
SUFFIX = ' (protein)'

In [3]:
# Set up logger
os.remove('spearman.standardized.interomics.min.power.' + CONDITION + '.pairs.all.miniDP3.log')
logger = logging.getLogger('analytics')

# Set the logging level
logger.setLevel(logging.INFO)

# Define a log format
formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')

# Create a console handler to output log messages to the console
console_handler = logging.StreamHandler()
console_handler.setFormatter(formatter)
logger.addHandler(console_handler)

# (Optional) Create a file handler to log messages to a file
file_handler = logging.FileHandler('spearman.standardized.interomics.min.power.' + CONDITION + '.pairs.all.miniDP3.log')
file_handler.setFormatter(formatter)
logger.addHandler(file_handler)

In [4]:
dfpb = pd.read_table('../../data/proteins-final-adjusted.csv', sep=',', dtype={'Patient-ID':str})
dfmb = pd.read_table('../../data/metabolites-final-adjusted.csv', sep=',', dtype={'Patient-ID':str})
dfmirna = pd.read_table('../../data/mirna-final-adjusted.csv', sep=',', dtype={'Patient-ID':str})
dftb = pd.read_table('../../data/transcripts-final-adjusted.csv', sep=',', dtype={'Patient-ID':str})
dfph = pd.read_table('../../data/PlacentalHistopathologyReportsCleaned.csv', sep=',', dtype={'Patient-ID':str})
dfph2 = pd.read_table('../../data/PlacentalHistopathologySlideFeaturesCleaned.csv', sep=',', dtype={'Patient-ID':str})

dfp_analyte = pd.read_table('../../data/protein-meta-final.csv', sep=',')
dfm_analyte = pd.read_table('../../data/metabolites-meta-final.csv', sep=',')
dfmirna_analyte = pd.read_table('../../data/mirna-meta-final.csv', sep=',')
dft_analyte = pd.read_table('../../data/transcripts-meta-final.csv', sep=',')

df_clinical = pd.read_table('../../data/metadata-final.csv', sep=',', dtype={'Study_ID/ID':str})
df_clinical = df_clinical[df_clinical['Condition']==CONDITION_CLINICAL_DF]

In [5]:
dfpb.shape, dfmb.shape, dfmirna.shape, dftb.shape, dfph.shape, dfph2.shape, df_clinical.shape

((321, 352),
 (319, 866),
 (294, 450),
 (294, 9585),
 (275, 6),
 (348, 9),
 (113, 21))

# Set up annotations

In [6]:
metabolites = {}
for index, row in dfm_analyte.iterrows():
    metabolites[row['CHEMICAL_NAME']] = {'name': row['CHEMICAL_NAME'], 'sub_group': row['SUB_PATHWAY'], 'super_group': row['SUPER_PATHWAY']}
    
miRNAs = {}
for index, row in dfmirna_analyte.iterrows():
    miRNAs[row['Transcript']] = {'name': row['Transcript'], 'sub_group': None, 'super_group': None}
    
proteins = {}
for index, row in dfp_analyte.iterrows():
    proteins[row['Assay'] + SUFFIX] = {'name': row['Assay'], 'sub_group': None, 'super_group': row['Panel']}
    
transcripts = {}
for index, row in dft_analyte.iterrows():
    transcripts[row['Transcript']] = {'name': row['Transcript'], 'sub_group': None, 'super_group': None}
    
histopathology = {}
for item in dfph:
    if item != 'Patient-ID':
        histopathology[item] = {'name': item, 'sub_group': None, 'super_group': None}
for item in dfph2:
    if item != 'Patient-ID':
        histopathology[item] = {'name': item, 'sub_group': None, 'super_group': None}
        
# print the number of included analytes
print('Histopathology Features:', str(len(histopathology)))
print('Metabolites:', str(len(metabolites)))
print('miRNAs:', str(len(miRNAs)))
print('Proteins:', str(len(proteins)))
print('Transcripts:', str(len(transcripts)))
print('Total:', str(len(histopathology)+len(metabolites)+len(miRNAs)+len(proteins)+len(transcripts)))

Histopathology Features: 13
Metabolites: 1032
miRNAs: 2414
Proteins: 452
Transcripts: 51174
Total: 55085


# Merge against prot/met data

In [7]:
dfm_analyte = list(set(metabolites.keys()).intersection(dfmb.columns))
dfmirna_analyte = list(set(miRNAs.keys()).intersection(dfmirna.columns))
dfp_analyte = list(set(proteins.keys()).intersection(dfpb.columns))
dft_analyte = list(set(transcripts.keys()).intersection(dftb.columns))
dfph_measurement = ['MVM', 'FVM', 'AI', 'CI', 'Placental Abnormality']
dfph_measurement2 = ['DVH', 'AVM', 'Syncytial Knots', 'Segmental Avascular Villi', 'DVM', 'Villitis of Unknown Etiology', 'Diffuse Villous Edema', 'Chorangiosis']

# Get all analytes together
analytes = dfph_measurement + dfph_measurement2 + dfm_analyte + dfmirna_analyte + dfp_analyte + dft_analyte

# print the number of included analytes that pass missingness threshold
print('Histopathology Features:', str(len(dfph_measurement)+len(dfph_measurement2)))
print('Metabolites:', str(len(dfm_analyte)))
print('miRNAs:', str(len(dfmirna_analyte)))
print('Proteins:', str(len(dfp_analyte)))
print('Transcripts:', str(len(dft_analyte)))
print('Total:', str(len(analytes)))

Histopathology Features: 13
Metabolites: 865
miRNAs: 448
Proteins: 343
Transcripts: 9582
Total: 11251


In [8]:
df_clinical.head()

Patient-ID Condition  LaborInitiation  MaternalAge  isWhite  isBlack   
14    MJ-0061   Control                1         27.0      1.0      0.0  \
18    MJ-0088   Control                1         32.0      1.0      0.0   
19    MJ-0093   Control                1         30.0      1.0      0.0   
24    MJ-0287   Control                0         20.0      0.0      1.0   
25    MJ-0295   Control                0         28.0      1.0      0.0   

    isAsian  Ethnicity    WksGest  PregravidBMI  ...  Para  LaborOnset   
14      0.0       -1.0  40.714286     22.061568  ...   0.0         0.0  \
18      0.0        0.0  39.714286     26.346494  ...   1.0         0.0   
19      0.0        0.0  40.142857           NaN  ...   1.0         0.0   
24      0.0       -1.0  39.142857     28.311014  ...   1.0         1.0   
25      0.0        0.0  39.000000     29.342682  ...   1.0         1.0   

    Smoker  IllicitDrugUser  DeliveryMethod  PregnancyRelatedHypertension   
14     0.0              0.0             0.0                             0  \
18     0.0              0.0             0.0                             0   
19     0.0              0.0             0.0                             0   
24     1.0              1.0             1.0                             0   
25     0.0              0.0             1.0                             0   

    FetalGrowthRestriction  Preeclampsia  InfSex  Birthweight  
14                       0             0     1.0       3480.0  
18                       0             0     0.0       3260.0  
19                       0             0     1.0       3355.0  
24                       0             0     1.0       3167.0  
25                       0             0     0.0       3750.0  

[5 rows x 21 columns]

In [9]:
df = df_clinical.merge(dfph[['Patient-ID'] + list(dfph_measurement)], on=['Patient-ID'], how='left')
print(df.shape)
df = df.merge(dfph2[['Patient-ID'] + list(dfph_measurement2)], on=['Patient-ID'], how='left')
print(df.shape)
df = df.merge(dfpb[['Patient-ID'] + list(dfp_analyte)], on=['Patient-ID'], how='inner')
print(df.shape)
df = df.merge(dfmb[['Patient-ID'] + list(dfm_analyte)], on=['Patient-ID'], how='left')
print(df.shape)
df = df.merge(dfmirna[['Patient-ID'] + list(dfmirna_analyte)], on=['Patient-ID'], how='left')
print(df.shape)
df = df.merge(dftb[['Patient-ID'] + list(dft_analyte)], on=['Patient-ID'], how='left')
print(df.shape)
df = df.fillna(-1)

(113, 26)
(113, 34)
(113, 377)
(113, 1242)
(113, 1690)
(113, 11272)


In [10]:
df.shape, dfpb.shape, dfmb.shape, dfmirna.shape, dftb.shape, dfph.shape, dfph2.shape, df_clinical.shape

((113, 11272),
 (321, 352),
 (319, 866),
 (294, 450),
 (294, 9585),
 (275, 6),
 (348, 9),
 (113, 21))

In [11]:
# Select a random subset of rows
np.random.seed(123)
num_rows_to_select = 30  # Set to smallest sample size
df = df.sample(n=num_rows_to_select)

In [12]:
df.shape

(30, 11272)

In [13]:
df['InfSex'].value_counts()

InfSex
1.0    16
0.0    14
Name: count, dtype: int64

In [14]:
df['isWhite'].value_counts()

isWhite
1.0    24
0.0     6
Name: count, dtype: int64

In [15]:
df['isBlack'].value_counts()

isBlack
0.0    27
1.0     3
Name: count, dtype: int64

In [16]:
df['isAsian'].value_counts()

isAsian
0.0    29
1.0     1
Name: count, dtype: int64

In [17]:
df.head()

Patient-ID Condition  LaborInitiation  MaternalAge  isWhite  isBlack   
104  Mini-DP-092   Control                1         35.0      1.0      0.0  \
87   Mini-DP-075   Control                0         35.0      1.0      0.0   
42   Mini-DP-028   Control                1         34.0      1.0      0.0   
82   Mini-DP-070   Control                0         26.0      0.0      1.0   
93   Mini-DP-081   Control                1         28.0      0.0      0.0   

     isAsian  Ethnicity    WksGest  PregravidBMI  ...   LENG8   FBXW4  MRPL22   
104      0.0        0.0  37.571429     24.428161  ...  5558.0   737.0   168.0  \
87       0.0        0.0  38.428571     25.777778  ...  5280.0  1236.0   245.0   
42       0.0        0.0  39.428571     24.805833  ...  4396.0   707.0   148.0   
82       0.0        0.0  40.714286     24.842781  ...  5204.0   661.0   215.0   
93       0.0        1.0  37.714286     26.222222  ...  2627.0   996.0   246.0   

     ENSG00000189229    MYL6  PRKAG1  HIGD1A      NR6A1  MAPK3  LMOD1  
104            243.0  1218.0   336.0   305.0  251.00000  543.0  185.0  
87             380.0  2144.0   572.0   535.0  279.00000  592.0  211.0  
42             267.0  1357.0   334.0   227.0  171.00000  480.0  235.0  
82             330.0  2275.0   394.0   290.0  181.93899  852.0  599.0  
93             131.0  1751.0   487.0   458.0  279.00000  560.0  109.0  

[5 rows x 11272 columns]

# Correlation network

In [18]:
import statsmodels.api as sm
import statsmodels.formula.api as smf
import statsmodels.sandbox.stats.multicomp
from statsmodels.genmod.families import family, links
import itertools

In [19]:
drop_cols = ['Patient-ID', 'Grav', 'DeliveryMethod', 
             'Para', 'PrePregWt_Kg', 'Ethnicity', 'isAsian', 
             'isBlack', 'WksGest', 'Condition', 'isWhite', 
             'Race', 'MaternalAge', 'Smoke', 'PregravidBMI',
             'HeightMeters']

# Pairwise GLM

In [20]:
def count_pairs(dat, analytes, proteins, metabolites, mirnas, transcripts, histopathology):

    # Create all possible pairs of inputs
    pairs = list(itertools.combinations(analytes, 2))
    logger.info('Created {} pairs'.format(len(pairs)))
         
    count = 0 
    done = 0
    skipped = 0
    completed = 0

    results = []
    columns = list(dat.columns)

    start_time = datetime.now()
    for (col1, col2) in pairs:

        if (col1 == col2):
            continue
                    
        if (col1 in histopathology.keys()) and (col2 in histopathology.keys()):
            continue
        
        if (col1 in metabolites.keys()) and (col2 in metabolites.keys()):
            continue
            
        if (col1 in mirnas.keys()) and (col2 in mirnas.keys()):
            continue

        if (col1 in proteins.keys()) and (col2 in proteins.keys()):
            continue
        
        if (col1 in transcripts.keys()) and (col2 in transcripts.keys()):
            continue
            
        if (col1 in proteins.keys()):
            name1 = proteins[col1]['name']
            subgroup1 = proteins[col1]['sub_group'] 
            supergroup1 = proteins[col1]['super_group']
            type1 = 'protein'
        elif (col1 in metabolites.keys()):
            name1 = metabolites[col1]['name']
            subgroup1 = metabolites[col1]['sub_group'] 
            supergroup1 = metabolites[col1]['super_group']
            type1 = 'metabolite'
        elif (col1 in mirnas.keys()):
            name1 = mirnas[col1]['name']
            subgroup1 = mirnas[col1]['sub_group'] 
            supergroup1 = mirnas[col1]['super_group']
            type1 = 'miRNA'
        elif (col1 in transcripts.keys()):
            name1 = transcripts[col1]['name']
            subgroup1 = transcripts[col1]['sub_group'] 
            supergroup1 = transcripts[col1]['super_group']
            type1 = 'transcript'
        elif (col1 in histopathology.keys()):
            name1 = histopathology[col1]['name']
            subgroup1 = histopathology[col1]['sub_group'] 
            supergroup1 = histopathology[col1]['super_group']
            type1 = 'histopathology'

        else:
            logger.warning('Col1 {} not found in any annotation'.format(col1))
            name1 = None
            subgroup1 = None
            supergroup1 = None
            type1 = None
            
        if (col2 in proteins.keys()):
            name2 = proteins[col2]['name']
            subgroup2 = proteins[col2]['sub_group'] 
            supergroup2 = proteins[col2]['super_group']
            type2 = 'protein'
        elif (col2 in metabolites.keys()):
            name2 = metabolites[col2]['name']
            subgroup2 = metabolites[col2]['sub_group'] 
            supergroup2 = metabolites[col2]['super_group']
            type2 = 'metabolite'
        elif (col2 in mirnas.keys()):
            name2 = mirnas[col2]['name']
            subgroup2 = mirnas[col2]['sub_group'] 
            supergroup2 = mirnas[col2]['super_group']
            type2 = 'miRNA'
        elif (col2 in transcripts.keys()):
            name2 = transcripts[col2]['name']
            subgroup2 = transcripts[col2]['sub_group'] 
            supergroup2 = transcripts[col2]['super_group']
            type2 = 'transcript'
        elif (col2 in histopathology.keys()):
            name2 = histopathology[col2]['name']
            subgroup2 = histopathology[col2]['sub_group'] 
            supergroup2 = histopathology[col2]['super_group']
            type2 = 'histopathology'
    
        else:
            logger.warning('Col2 {} not found in any annotation'.format(col2))
            name2 = None
            subgroup2 = None
            supergroup2 = None
            type2 = None
            
        count += 1
        
    print('Running {} pairs'.format(count))

count_pairs(df, analytes, proteins, metabolites, miRNAs, transcripts, histopathology)

2024-02-11 11:35:10,550 - analytics - INFO - Created 63286875 pairs


Running 16851765 pairs


In [21]:
def evaluate_effect_size(df, logger):
    # evaluate effect size - cohen's d
    df_no_effect = df[abs(df['coef'])<0.01]
    df_very_small = df[abs(df['coef'])>=0.01]
    df_very_small = df_very_small[abs(df_very_small['coef'])<0.1]
    df_small = df[abs(df['coef'])>=0.1]
    df_small = df_small[abs(df_small['coef'])<0.2]
    df_medium = df[abs(df['coef'])>=0.2]
    df_medium  = df_medium[abs(df_medium['coef'])<0.3]
    df_medium_large = df[abs(df['coef'])>=0.3]
    df_medium_large = df_medium_large[abs(df_medium_large['coef'])<0.5]
    df_large = df[abs(df['coef'])>=0.5]
    df_large = df_large[abs(df_large['coef'])<0.7]
    df_very_large = df[abs(df['coef'])>=0.7]
    df_very_large = df_very_large[abs(df_very_large['coef'])<0.9]
    df_huge = df[abs(df['coef'])>=0.9]
    
    # print info on effect sizes
    logger.info('Number of Analyte Pairs with No Monotonic Relationship: {}'.format(str(df_no_effect.shape[0])))
    logger.info('Number of Analyte Pairs with Very Weak Monotonic Relationship: {}'.format(str(df_very_small.shape[0])))
    logger.info('Number of Analyte Pairs with Weak Monotonic Relationship: {}'.format(str(df_small.shape[0])))
    logger.info('Number of Analyte Pairs with Moderate Monotonic Relationship: {}'.format(str(df_medium.shape[0])))
    logger.info('Number of Analyte Pairs with Moderate Strong Monotonic Relationship: {}'.format(str(df_medium_large.shape[0])))
    logger.info('Number of Analyte Pairs with Strong Monotonic Relationship: {}'.format(str(df_large.shape[0])))
    logger.info('Number of Analyte Pairs with Very Strong Monotonic Relationship: {}'.format(str(df_very_large.shape[0])))
    logger.info('Number of Analyte Pairs with Near Perfect Monotonic Relationship: {}'.format(str(df_huge.shape[0])))
    logger.info('\n')
    

def run_spearman_pairwise(dat, condition, analytes, proteins, metabolites, mirnas, transcripts, histopathology, max_run=None):

    # Create all possible pairs of inputs
    pairs = list(itertools.combinations(analytes, 2))
    logger.info('Created {} pairs'.format(len(pairs)))
    
    f_failed = open('failed.spearman.standardized.interomics.min.power.' + condition + '.pairs.all.miniDP3.txt', mode='w')
    f_output = 'spearman.standardized.interomics.min.power.' + condition + '.all.miniDP3.txt'
    f_output_sig = 'spearman.standardized.interomics.min.power.' + condition + '.sig.miniDP3.txt'
         
    count = 0 
    done = 0
    skipped = 0
    completed = 0

    results = []
    columns = list(dat.columns)

    start_time = datetime.now()
    for (col1, col2) in pairs:

        if (col1 == col2):
            continue
                           
        if (col1 in histopathology.keys()) and (col2 in histopathology.keys()):
            continue
        
        if (col1 in metabolites.keys()) and (col2 in metabolites.keys()):
            continue
            
        if (col1 in mirnas.keys()) and (col2 in mirnas.keys()):
            continue

        if (col1 in proteins.keys()) and (col2 in proteins.keys()):
            continue
        
        if (col1 in transcripts.keys()) and (col2 in transcripts.keys()):
            continue

        if (col1 in proteins.keys()):
            name1 = proteins[col1]['name']
            subgroup1 = proteins[col1]['sub_group'] 
            supergroup1 = proteins[col1]['super_group']
            type1 = 'protein'
        elif (col1 in metabolites.keys()):
            name1 = metabolites[col1]['name']
            subgroup1 = metabolites[col1]['sub_group'] 
            supergroup1 = metabolites[col1]['super_group']
            type1 = 'metabolite'
        elif (col1 in mirnas.keys()):
            name1 = mirnas[col1]['name']
            subgroup1 = mirnas[col1]['sub_group'] 
            supergroup1 = mirnas[col1]['super_group']
            type1 = 'miRNA'
        elif (col1 in transcripts.keys()):
            name1 = transcripts[col1]['name']
            subgroup1 = transcripts[col1]['sub_group'] 
            supergroup1 = transcripts[col1]['super_group']
            type1 = 'transcript'
        elif (col1 in histopathology.keys()):
            name1 = histopathology[col1]['name']
            subgroup1 = histopathology[col1]['sub_group'] 
            supergroup1 = histopathology[col1]['super_group']
            type1 = 'histopathology'
        else:
            logger.warning('Col1 {} not found in any annotation'.format(col1))
            name1 = None
            subgroup1 = None
            supergroup1 = None
            type1 = None
            
        if (col2 in proteins.keys()):
            name2 = proteins[col2]['name']
            subgroup2 = proteins[col2]['sub_group'] 
            supergroup2 = proteins[col2]['super_group']
            type2 = 'protein'
        elif (col2 in metabolites.keys()):
            name2 = metabolites[col2]['name']
            subgroup2 = metabolites[col2]['sub_group'] 
            supergroup2 = metabolites[col2]['super_group']
            type2 = 'metabolite'
        elif (col2 in mirnas.keys()):
            name2 = mirnas[col2]['name']
            subgroup2 = mirnas[col2]['sub_group'] 
            supergroup2 = mirnas[col2]['super_group']
            type2 = 'miRNA'
        elif (col2 in transcripts.keys()):
            name2 = transcripts[col2]['name']
            subgroup2 = transcripts[col2]['sub_group'] 
            supergroup2 = transcripts[col2]['super_group']
            type2 = 'transcript'
        elif (col2 in histopathology.keys()):
            name2 = histopathology[col2]['name']
            subgroup2 = histopathology[col2]['sub_group'] 
            supergroup2 = histopathology[col2]['super_group']
            type2 = 'histopathology'
        else:
            logger.warning('Col2 {} not found in any annotation'.format(col2))
            name2 = None
            subgroup2 = None
            supergroup2 = None
            type2 = None

        sub = dat[['Patient-ID', col1, col2]].copy()
        sub.rename(columns={col1:'analyte1'}, inplace=True)
        sub.rename(columns={col2:'analyte2'}, inplace=True)


        if (sub['analyte1'].skew() > 1.5) | (sub['analyte1'].skew() < -1.5):

            #logger.info('Setting gamma family for skewed analyte %s'%(col))

            # Set any zero values to 1/2 the smallest value
            sub.loc[sub['analyte1']==0, 'analyte1'] = (sub.loc[sub['analyte1']>0, 'analyte1'].min() / 2.0)
            

        # z-score transform dependent variable data
        if col2 not in histopathology.keys():
            sub['analyte2'] = sub['analyte2'].astype(np.float64)
            sub['analyte2'] = (sub['analyte2'] - sub['analyte2'].mean() ) / sub['analyte2'].std()

            
        try:
            coef, p = scipy.stats.spearmanr(sub['analyte1'], sub['analyte2'])
            results.append((col1, name1, type1, supergroup1, subgroup1, col2, name2, type2, supergroup2, subgroup2, coef, p))
            completed += 1

        except Exception as e:
            logger.info('Failed analytes {} {} with error {}'.format(col1, col2, str(e)))
            f_failed.write(col1 + '\t' + col2 + '\n')
            
            
        count += 1
        if (max_run is not None) and (count >= max_run):
            break
        
        if (count % 1000) == 0:
            elapsed_time = datetime.now() - start_time    
            logger.info('Finished {} in {:.3f} seconds (skipped {})'.format(count, elapsed_time.total_seconds(), skipped))
            
    df = pd.DataFrame(results, columns=['col1', 'name1', 'type1', 'supergroup1', 'subgroup1', 'col2', 'name2', 'type2', 'supergroup2', 'subgroup2', 'coef', 'p-value'])
    df.sort_values(['p-value'], ascending=True, inplace=True)
    f_failed.close()

    np.seterr(all='warn')
    logger.info('\nFinished analyzing all {} pairs!'.format(str(count)))
    logger.info('Number of analyte pairs with converged formula: {}'.format(str(df.shape[0])))
    (adj_pval_index, adj_pval, _, _) = statsmodels.sandbox.stats.multicomp.multipletests(df.loc[~df['p-value'].isnull(), 'p-value'], alpha=0.05, method='fdr_bh')
    df.loc[~df['p-value'].isnull(), 'pval_adj'] = adj_pval
    df.sort_values(['pval_adj'], ascending=True, inplace=True)
    df.to_csv(f_output, index=False, sep='\t')
    
    # filter for significance
    #df = df[df['pval_adj']<0.05]  #benjammini-hochman
    bonferroni_correction = 0.05/count
    df = df[df['p-value']<bonferroni_correction]  #bonferroni correction
    logger.info('\nBonferroni Correction: p<{}'.format(str(bonferroni_correction)))
    logger.info('Number of analyte pairs whose levels are significantly associated: {}'.format(str(df.shape[0])))
    df.to_csv(f_output_sig, index=False, sep='\t')
    
    # evaluate effect size - cohen's d
    logger.info('Effect Sizes (Cohen\'s D ) For Significant Correlations:')
    evaluate_effect_size(df, logger)
    logger.info('\nFinished all correlation analyses!')
    
    return df

In [22]:
os.remove('failed.spearman.standardized.interomics.min.power.' + CONDITION + '.pairs.all.miniDP3.txt')
os.remove('spearman.standardized.interomics.min.power.' + CONDITION + '.all.miniDP3.txt')
os.remove('spearman.standardized.interomics.min.power.' + CONDITION + '.sig.miniDP3.txt')

In [23]:
spearman_pairwise = run_spearman_pairwise(df, CONDITION, analytes, proteins, metabolites, miRNAs, transcripts, histopathology)

2024-02-11 11:36:13,518 - analytics - INFO - Created 63286875 pairs
2024-02-11 11:36:15,796 - analytics - INFO - Finished 1000 in 2.274 seconds (skipped 0)
2024-02-11 11:36:18,205 - analytics - INFO - Finished 2000 in 4.683 seconds (skipped 0)
2024-02-11 11:36:20,993 - analytics - INFO - Finished 3000 in 7.471 seconds (skipped 0)
2024-02-11 11:36:23,339 - analytics - INFO - Finished 4000 in 9.818 seconds (skipped 0)
2024-02-11 11:36:25,672 - analytics - INFO - Finished 5000 in 12.151 seconds (skipped 0)
2024-02-11 11:36:27,991 - analytics - INFO - Finished 6000 in 14.469 seconds (skipped 0)
2024-02-11 11:36:30,311 - analytics - INFO - Finished 7000 in 16.790 seconds (skipped 0)
2024-02-11 11:36:32,460 - analytics - INFO - Finished 8000 in 18.939 seconds (skipped 0)
2024-02-11 11:36:34,615 - analytics - INFO - Finished 9000 in 21.094 seconds (skipped 0)
2024-02-11 11:36:36,885 - analytics - INFO - Finished 10000 in 23.364 seconds (skipped 0)
2024-02-11 11:36:39,210 - analytics - INFO - 

/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the

/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the

/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the

/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  warnings.warn(stats.ConstantInputWarning(warn_msg))
/usr/local/lib/python3.11/site-packages/scipy/stats/_stats_py.py:4916: ConstantInputWarning: An input array is constant; the

...

2024-02-11 15:18:31,795 - analytics - INFO - Finished 5312000 in 13338.274 seconds (skipped 0)
2024-02-11 15:18:34,793 - analytics - INFO - Finished 5313000 in 13341.272 seconds (skipped 0)
2024-02-11 15:18:37,672 - analytics - INFO - Finished 5314000 in 13344.151 seconds (skipped 0)
2024-02-11 15:18:40,602 - analytics - INFO - Finished 5315000 in 13347.081 seconds (skipped 0)
2024-02-11 15:18:43,786 - analytics - INFO - Finished 5316000 in 13350.264 seconds (skipped 0)
2024-02-11 15:18:46,538 - analytics - INFO - Finished 5317000 in 13353.017 seconds (skipped 0)
2024-02-11 15:18:49,380 - analytics - INFO - Finished 5318000 in 13355.859 seconds (skipped 0)
2024-02-11 15:18:52,196 - analytics - INFO - Finished 5319000 in 13358.675 seconds (skipped 0)
2024-02-11 15:18:54,978 - analytics - INFO - Finished 5320000 in 13361.457 seconds (skipped 0)
2024-02-11 15:18:57,877 - analytics - INFO - Finished 5321000 in 13364.356 seconds (skipped 0)
2024-02-11 15:19:00,682 - analytics - INFO - Finis

2024-02-11 15:22:17,779 - analytics - INFO - Finished 5399000 in 13564.258 seconds (skipped 0)
2024-02-11 15:22:20,012 - analytics - INFO - Finished 5400000 in 13566.491 seconds (skipped 0)
2024-02-11 15:22:22,546 - analytics - INFO - Finished 5401000 in 13569.025 seconds (skipped 0)
2024-02-11 15:22:24,812 - analytics - INFO - Finished 5402000 in 13571.291 seconds (skipped 0)
2024-02-11 15:22:27,131 - analytics - INFO - Finished 5403000 in 13573.610 seconds (skipped 0)
2024-02-11 15:22:29,418 - analytics - INFO - Finished 5404000 in 13575.897 seconds (skipped 0)
2024-02-11 15:22:31,759 - analytics - INFO - Finished 5405000 in 13578.238 seconds (skipped 0)
2024-02-11 15:22:34,014 - analytics - INFO - Finished 5406000 in 13580.492 seconds (skipped 0)
2024-02-11 15:22:36,282 - analytics - INFO - Finished 5407000 in 13582.761 seconds (skipped 0)
2024-02-11 15:22:38,586 - analytics - INFO - Finished 5408000 in 13585.065 seconds (skipped 0)
2024-02-11 15:22:40,901 - analytics - INFO - Finis

2024-02-11 15:25:45,608 - analytics - INFO - Finished 5486000 in 13772.087 seconds (skipped 0)
2024-02-11 15:25:48,398 - analytics - INFO - Finished 5487000 in 13774.877 seconds (skipped 0)
2024-02-11 15:25:51,101 - analytics - INFO - Finished 5488000 in 13777.580 seconds (skipped 0)
2024-02-11 15:25:53,274 - analytics - INFO - Finished 5489000 in 13779.753 seconds (skipped 0)
2024-02-11 15:25:55,412 - analytics - INFO - Finished 5490000 in 13781.890 seconds (skipped 0)
2024-02-11 15:25:57,695 - analytics - INFO - Finished 5491000 in 13784.174 seconds (skipped 0)
2024-02-11 15:25:59,927 - analytics - INFO - Finished 5492000 in 13786.406 seconds (skipped 0)
2024-02-11 15:26:02,223 - analytics - INFO - Finished 5493000 in 13788.702 seconds (skipped 0)
2024-02-11 15:26:04,496 - analytics - INFO - Finished 5494000 in 13790.975 seconds (skipped 0)
2024-02-11 15:26:06,838 - analytics - INFO - Finished 5495000 in 13793.317 seconds (skipped 0)
2024-02-11 15:26:09,124 - analytics - INFO - Finis

2024-02-11 15:29:35,691 - analytics - INFO - Finished 5573000 in 14002.169 seconds (skipped 0)
2024-02-11 15:29:37,942 - analytics - INFO - Finished 5574000 in 14004.421 seconds (skipped 0)
2024-02-11 15:29:40,266 - analytics - INFO - Finished 5575000 in 14006.745 seconds (skipped 0)
2024-02-11 15:29:42,575 - analytics - INFO - Finished 5576000 in 14009.054 seconds (skipped 0)
2024-02-11 15:29:44,986 - analytics - INFO - Finished 5577000 in 14011.464 seconds (skipped 0)
2024-02-11 15:29:47,289 - analytics - INFO - Finished 5578000 in 14013.768 seconds (skipped 0)
2024-02-11 15:29:49,613 - analytics - INFO - Finished 5579000 in 14016.092 seconds (skipped 0)
2024-02-11 15:29:51,988 - analytics - INFO - Finished 5580000 in 14018.467 seconds (skipped 0)
2024-02-11 15:29:54,287 - analytics - INFO - Finished 5581000 in 14020.766 seconds (skipped 0)
2024-02-11 15:29:56,608 - analytics - INFO - Finished 5582000 in 14023.087 seconds (skipped 0)
2024-02-11 15:29:58,909 - analytics - INFO - Finis

2024-02-11 15:33:09,899 - analytics - INFO - Finished 5660000 in 14216.377 seconds (skipped 0)
2024-02-11 15:33:12,692 - analytics - INFO - Finished 5661000 in 14219.171 seconds (skipped 0)
2024-02-11 15:33:15,446 - analytics - INFO - Finished 5662000 in 14221.925 seconds (skipped 0)
2024-02-11 15:33:18,179 - analytics - INFO - Finished 5663000 in 14224.657 seconds (skipped 0)
2024-02-11 15:33:21,163 - analytics - INFO - Finished 5664000 in 14227.642 seconds (skipped 0)
2024-02-11 15:33:23,792 - analytics - INFO - Finished 5665000 in 14230.271 seconds (skipped 0)
2024-02-11 15:33:26,129 - analytics - INFO - Finished 5666000 in 14232.608 seconds (skipped 0)
2024-02-11 15:33:28,420 - analytics - INFO - Finished 5667000 in 14234.899 seconds (skipped 0)
2024-02-11 15:33:30,780 - analytics - INFO - Finished 5668000 in 14237.259 seconds (skipped 0)
2024-02-11 15:33:33,237 - analytics - INFO - Finished 5669000 in 14239.716 seconds (skipped 0)
2024-02-11 15:33:35,434 - analytics - INFO - Finis

In [24]:
spearman_pairwise = pd.read_csv('spearman.standardized.interomics.min.power.' + CONDITION + '.sig.miniDP3.txt', sep='\t')

In [25]:
spearman_pairwise['coef'].hist(range=[-1, 1])

In [26]:
abs(spearman_pairwise['coef']).hist(range=[0, 1])

In [27]:
# filter for effect
df_no_effect = spearman_pairwise[abs(spearman_pairwise['coef'])<0.01]
df_very_small = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.01]
df_very_small = df_very_small[abs(df_very_small['coef'])<0.1]
df_effect = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.1]
print('\nNumber of analyte pairs whose effect size is at least weak: '.format(str(df_effect.shape[0])))


# evaluate effect size - cohen's d
df_small = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.1]
df_small = df_small[abs(df_small['coef'])<0.2]
df_medium = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.2]
df_medium  = df_medium[abs(df_medium['coef'])<0.3]
df_medium_large = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.3]
df_medium_large = df_medium_large[abs(df_medium_large['coef'])<0.5]
df_large = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.5]
df_large = df_large[abs(df_large['coef'])<0.7]
df_very_large = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.7]
df_very_large = df_very_large[abs(df_very_large['coef'])<0.9]
df_huge = spearman_pairwise[abs(spearman_pairwise['coef'])>=0.9]

# print info on effect sizes
print('Number of Analyte Pairs with No Monotonic Relationship: {}'.format(str(df_no_effect.shape[0])))
print('Number of Analyte Pairs with Very Weak Monotonic Relationship: {}'.format(str(df_very_small.shape[0])))
print('Number of Analyte Pairs with Weak Monotonic Relationship: {}'.format(str(df_small.shape[0])))
print('Number of Analyte Pairs with Moderate Monotonic Relationship: {}'.format(str(df_medium.shape[0])))
print('Number of Analyte Pairs with Moderate Strong Monotonic Relationship: {}'.format(str(df_medium_large.shape[0])))
print('Number of Analyte Pairs with Strong Monotonic Relationship: {}'.format(str(df_large.shape[0])))
print('Number of Analyte Pairs with Very Strong Monotonic Relationship: {}'.format(str(df_very_large.shape[0])))
print('Number of Analyte Pairs with Near Perfect Monotonic Relationship: {}'.format(str(df_huge.shape[0])))